In [1]:
import numpy as np
import csv
from sklearn.cross_validation import cross_val_score
from sklearn.linear_model import LogisticRegression
from sklearn.externals import joblib
from sklearn.metrics import roc_curve, auc
from sklearn.cross_validation import train_test_split
from sklearn.cross_validation import StratifiedKFold
from scipy import interp
from  matplotlib import pyplot as plt
from sklearn import cross_validation
import pandas as pd
from sklearn.metrics import roc_auc_score
from sklearn import metrics, preprocessing
import pickle
import matplotlib.pyplot as plt
import matplotlib.cm as cm
%matplotlib inline

In [2]:
df = pd.read_json("~/Documents/AML/HW2/train.json")

In [3]:
df.head(5)

cuisine     id                                        ingredients
0        greek  10259  [romaine lettuce, black olives, grape tomatoes...
1  southern_us  25693  [plain flour, ground pepper, salt, tomatoes, g...
2     filipino  20130  [eggs, pepper, salt, mayonaise, cooking oil, g...
3       indian  22213                [water, vegetable oil, wheat, salt]
4       indian  13162  [black pepper, shallots, cornflour, cayenne pe...

In [4]:
ingredients_list = df['ingredients'].as_matrix()

In [5]:
len(ingredients_list)

39774

In [19]:
string = 'Chinese rice vinegar'

In [20]:
string.lower()

'chinese rice vinegar'

In [6]:
def divide_phrases(matrix):
    for array in matrix:
        for ingr in array:
            if ' ' in ingr:
#                 print(ingr)
                new_ingr_split = ingr.split()
#                 print(new_ingr_split)
                for item in new_ingr_split:
                    array.append(item)

In [7]:
divide_phrases(ingredients_list)

['romaine', 'lettuce']
['black', 'olives']
['grape', 'tomatoes']
['purple', 'onion']
['garbanzo', 'beans']
['feta', 'cheese', 'crumbles']
['plain', 'flour']
['ground', 'pepper']
['ground', 'black', 'pepper']
['green', 'tomatoes']
['yellow', 'corn', 'meal']
['vegetable', 'oil']
['cooking', 'oil']
['green', 'chilies']
['grilled', 'chicken', 'breasts']
['garlic', 'powder']
['yellow', 'onion']
['soy', 'sauce']
['chicken', 'livers']
['vegetable', 'oil']
['black', 'pepper']
['cayenne', 'pepper']
['garlic', 'paste']
['lemon', 'juice']
['chili', 'powder']
['ground', 'cumin']
['boneless', 'chicken', 'skinless', 'thigh']
['garam', 'masala']
['double', 'cream']
['natural', 'yogurt']
['bay', 'leaf']
['plain', 'flour']
['fresh', 'ginger', 'root']
['ground', 'cinnamon']
['vanilla', 'extract']
['ground', 'ginger']
['powdered', 'sugar']
['baking', 'powder']
['olive', 'oil']
['medium', 'shrimp']
['chopped', 'cilantro']
['jalapeno', 'chilies']
['flat', 'leaf', 'parsley']
['skirt', 'steak']
['white', 'vi

In [8]:
ingredients_list[0:2]

array([ ['romaine lettuce', 'black olives', 'grape tomatoes', 'garlic', 'pepper', 'purple onion', 'seasoning', 'garbanzo beans', 'feta cheese crumbles', 'romaine', 'lettuce', 'black', 'olives', 'grape', 'tomatoes', 'purple', 'onion', 'garbanzo', 'beans', 'feta', 'cheese', 'crumbles'],
       ['plain flour', 'ground pepper', 'salt', 'tomatoes', 'ground black pepper', 'thyme', 'eggs', 'green tomatoes', 'yellow corn meal', 'milk', 'vegetable oil', 'plain', 'flour', 'ground', 'pepper', 'ground', 'black', 'pepper', 'green', 'tomatoes', 'yellow', 'corn', 'meal', 'vegetable', 'oil']], dtype=object)

In [11]:
def drop_spaces_or_fillers(matrix):
    for array in matrix:
        for ingred in array:
            if ' ' in ingred:
                array.remove(ingred)
            elif ingred == 'the' or ingred == 'of' or ingred == 'and' or ingred == 'a':
                array.remove(ingred)

In [12]:
drop_spaces_or_fillers(ingredients_list)

In [14]:
ingredients_list[-3:-1]

array([ ['eggs', 'raisins', 'flour', 'sugar', 'salt', 'milk', 'butter', 'citrus', 'fruit', 'sourdough', 'starter', 'hot', 'tea', 'ground', 'nutmeg', 'ground', 'cinnamon'],
       ['minced garlic', 'baking powder', 'dark soy sauce', 'peanuts', 'flour', 'scallions', 'vodka', 'egg whites', 'broccoli', 'sugar', 'baking soda', 'oil', 'boneless', 'chicken', 'skinless', 'thigh', 'minced', 'garlic', 'steamed', 'white', 'rice', 'baking', 'powder', 'corn', 'starch', 'dark', 'soy', 'sauce', 'kosher', 'salt', 'Chinese', 'rice', 'vinegar', 'fresh', 'ginger', 'egg', 'whites', 'toasted', 'sesame', 'seeds', 'store', 'bought', 'low', 'sodium', 'chicken', 'stock', 'baking', 'soda', 'Shaoxing', 'wine']], dtype=object)

In [22]:
def convert_lowercase(matrix):
    i = 0
    j = 0
    while i < len(matrix):
        while j < len(matrix[i]):
            matrix[i][j].lower()
            j+=1
        i+=1

In [23]:
convert_lowercase(ingredients_list[-3:-1])

In [24]:
print(ingredients_list[-3:-1])

[ ['eggs', 'raisins', 'flour', 'sugar', 'salt', 'milk', 'butter', 'citrus', 'fruit', 'sourdough', 'starter', 'hot', 'tea', 'ground', 'nutmeg', 'ground', 'cinnamon']
 ['minced garlic', 'baking powder', 'dark soy sauce', 'peanuts', 'flour', 'scallions', 'vodka', 'egg whites', 'broccoli', 'sugar', 'baking soda', 'oil', 'boneless', 'chicken', 'skinless', 'thigh', 'minced', 'garlic', 'steamed', 'white', 'rice', 'baking', 'powder', 'corn', 'starch', 'dark', 'soy', 'sauce', 'kosher', 'salt', 'chinese', 'rice', 'vinegar', 'fresh', 'ginger', 'egg', 'whites', 'toasted', 'sesame', 'seeds', 'store', 'bought', 'low', 'sodium', 'chicken', 'stock', 'baking', 'soda', 'shaoxing', 'wine']]


In [25]:
ingredientDict = dict()

In [26]:
for item in ingredients_list:
    for ingredient in item:
        if ingredient in ingredientDict:
            ingredientDict[ingredient] +=1
        else:
            ingredientDict[ingredient] =1

In [27]:
len(ingredientDict)

7705

In [28]:
consolidated_list = list(ingredientDict.keys())

In [30]:
print (consolidated_list[-3:-1])

['ounc', 'shredded Italian cheese']
